Figures from clustering attempts
----------------------

### Author: BB
### Date: 200630

**This is a notebook comparing different clustering methods and their parameters, so see how "well" they cluster my dataset of ~1600 molecules from my Lon Virtual screening.**

Clustering methods:
1. Butina (rdkit implementation. Found out from Diogo) https://pubs.acs.org/doi/pdf/10.1021/ci9803381
2. MultiMCS (code I wrote, based on the algorithm)

Visualization methods:
1. MDS (scikit-learn implementation)
2. tSNE (scikit-learn implementation)

Molecules to be clustered:
1. 1388 unqiue SMILES (from ~1600 molecules)
2. 704 unique Murcko fragment SMILES (from the 1388 SMILES)



In [1]:
import sys
import tqdm
import itertools

from rdkit import DataStructs
from rdkit.ML.Cluster import Butina
from rdkit import Chem
from rdkit.Chem import (AllChem, Draw, rdFMCS)

import sklearn
from sklearn import manifold
from sklearn.decomposition import PCA

import numpy as np
import pandas as pd

import bokeh.io
import bokeh.plotting
import bokeh_catplot
import bokeh.palettes
palette1 = bokeh.palettes.Category20_20
bokeh.io.output_notebook()

Loading BokehJS ...

### Defining functions

In [2]:
# edited version
def butina_noprint(input_file_path,cutoff_val):
    """
    A function to import a list of SMILES and corresponding names (e.g. ZINC IDs) of molecules and a desired cutoff value
    to cluster the molecules based on an algorithm by Darko Butina  J. Chem. Inf. Comput. Sci. 1999, 39, 4, 747–750. 
    
    Return [0] : list of tuples, each tuple being a cluster and containing the indices of the molecules in the cluster
    Return [1] : list of SMILES strings in the order they were read from input file. Indices of return[0] should correspond to molecule SMILES.
    Return [2] : list of names in the order they were read from input file. Indices of return[0] should correspond to molecule name.
    
    Parameters
    -----------
    input_file_path : (str) path to file containig SMILES and names
    
    cutoff_val : (float) value from a range of 0 to 1. Will define the distance max cutoff
    
    Notes
    -------
    - Automatically checks for duplicate SMILES in the list of molecules, will discard duplicate after first occurence.
    - Molecules not belonging to a cluster, i.e. singletons, are grouped into the last "cluster" of singletons
    """
    fps = []
    zinc_ids = []
    smiles_list = []
    counter = 0
    with open(input_file_path) as f:
        for line in f:
            smiles = line.split()[0] 
            zinc = line.split()[1]
            # check for duplicates
            if smiles not in smiles_list:
                # generate mol and fingerprint
                mol = Chem.MolFromSmiles(smiles)
                fp = Chem.RDKFingerprint(mol)
                # append to lists
                fps.append(fp)        
                zinc_ids.append(zinc)
                smiles_list.append(smiles)
                counter += 1
                if counter % 100 == 0:
                    sys.stdout.write('\rParsed %8d smiles' % counter)
                    sys.stdout.flush()
    #print('Parsed %8d smiles' % counter)
    # first generate the distance matrix:
    #print('Generating distance matrix...')
    dists = []
    nfps = len(fps)
    for i in range(1,nfps):
        sims = DataStructs.BulkTanimotoSimilarity(fps[i],fps[:i])
        dists.extend([1-x for x in sims])
    # now cluster the data:
    #print('Clustering with Butina...')
# cutoff, n_clusters
#    0.5, 3126
#    0.7, 662
#    0.8, 173
    cutoff = cutoff_val
    cs = Butina.ClusterData(dists,nfps,cutoff,isDistData=True)
    #!mkdir representatives
    ### implementation of singleton to last "cluster". this won't be included in total # of clusters
    if len(cs) != 1:
        cs_final = [] 
        temp_list = []
        for cs_indiv in cs:
            if len(cs_indiv) == 1:
                temp_list.append(cs_indiv[0])
            else: 
                cs_final.append(cs_indiv)
        if len(temp_list) >= 1:
            cs_final.append(tuple(temp_list))
            singletons_added = 'yes'
            length_of_clusters = len(cs_final) - 1
        else:
            singletons_added = 'no'
            length_of_clusters = len(cs_final)
    else:
        cs_final = cs
        length_of_clusters = len(cs_final)
    for index,cluster in enumerate(cs_final):
        i = cluster[0]
        zinc = zinc_ids[i]
        mol = Chem.MolFromSmiles(smiles_list[i])
        #Draw.MolToFile(mol, 'representatives/%s.png' % zinc)
        #specifically for last "cluster" of singletons
        #if cluster == cs_final[-1] and cluster != cs_final[0] and singletons_added == 'yes':
            #print ('Cluster of singletons of length %d : ' % len(cluster), cluster)
        # for every other actual cluster
        #else:
            #print ('Cluster #%d of length %d : ' % (index, len(cluster)), cluster)  
    #print ('Total # of clusters %d' % length_of_clusters)
    return cs_final, smiles_list, zinc_ids, length_of_clusters
res1 = butina_noprint('list_of_20_smiles_right.txt',0.5)
res1[0]

[(12, 9, 10, 11, 15), (2, 5, 7), (16, 14, 13, 8, 6, 4, 3, 1, 0)]

In [3]:
# MultiMCS clustering with no duplicates no print. FIXED REDUNDANT MOLECULES BUG

input_file_path = 'list_of_20_smiles_right.txt'
def tanimoto_calculator_nodup_noprint(input_file_path, distData=False):
    """
    A function to import a list of SMILES and corresponding names (e.g. ZINC IDs) of molecules and a desired cutoff value
    to cluster the molecules based on an algorithm by Darko Butina  J. Chem. Inf. Comput. Sci. 1999, 39, 4, 747–750. 
    
    Return [0] : list of tuples, each tuple being a cluster and containing the indices of the molecules in the cluster
    Return [1] : list of SMILES strings in the order they were read from input file. Indices of return[0] should correspond to molecule SMILES.
    Return [2] : list of names in the order they were read from input file. Indices of return[0] should correspond to molecule name.
    
    Parameters
    -----------
    input_file_path : (str) path to file containig SMILES and names
    
    cutoff_val : (float) value from a range of 0 to 1. Will define the distance max cutoff
    
    Notes
    -------
    - Automatically checks for duplicate SMILES in the list of molecules, will discard duplicate after first occurence.
    - Molecules not belonging to a cluster, i.e. singletons, are grouped into the last "cluster" of singletons
    """
#while True:    
    fps = []
    zinc_ids = []
    smiles_list = []
    counter = 0

    with open(input_file_path) as f:
        for line in f:
            smiles = line.split()[0] 
            zinc = line.split()[1]
            # check for duplicates
            if smiles not in smiles_list:
                # generate mol and fingerprint
                mol = Chem.MolFromSmiles(smiles)
                fp = Chem.RDKFingerprint(mol)
                # append to lists
                fps.append(fp)        
                zinc_ids.append(zinc)
                smiles_list.append(smiles)
                counter += 1
                #if counter % 100 == 0:
                #    sys.stdout.write('\rParsed %8d smiles' % counter)
                #    sys.stdout.flush()
    #print('Parsed %8d smiles' % counter)
    # first generate the distance matrix:
    #print('Generating distance/Tanimoto matrix...')
    dists = []
    tani_matrix = []
    dist_labels = []
    nfps = len(fps)
    for i in range(1,nfps):
        sims = DataStructs.BulkTanimotoSimilarity(fps[i],fps[:i])
        dists.extend([1-x for x in sims])
        tani_matrix.extend([x for x in sims])
        dist_labels.extend([])
    #print('Distance data / Tanimoto similarities calculated.')
    #print('Length of matrix is: %d' %len(tani_matrix))
    if distData == True:
        return dists, smiles_list, zinc_ids
    else:
        return tani_matrix, smiles_list, zinc_ids
    #break
    
def MultiMCS_clustering_nodup_noprint(input_file_path, 
                        minTanimotoSimilarity=0.57, 
                        minClusterSize=3, 
                        minMCSSize=4,
                        completeRingsOnly=False,
                        ringMatchesRingOnly=False,
                        atomCompare=rdFMCS.AtomCompare.CompareAny,
                        bondCompare=rdFMCS.BondCompare.CompareOrderExact,
                        ringCompare=rdFMCS.RingCompare.IgnoreRingFusion):
    """
    A function that clusters molecules based on an algorithm by MultiMCS...
    """
    tani_matrix, smiles_list, zinc_ids = tanimoto_calculator_nodup_noprint(input_file_path, distData=False) 
    # Making indices i and k for Pandas DataFrame to use
    i_column = []
    k_column = []
    length_of_smiles = len(smiles_list)
    for i in range(length_of_smiles):
        for k in range(i):
            i_column.append(i)
            k_column.append(k)
    # Generating DataFrame containing Tanimoto similarity coeffs and indicies i and k to designate molecule pairs. All molecules are valid to start with 
    # Also checking if Tanimoto value is above defined cutoff. Anything above cutoff will is valid clustering and anything below is invalid
    df = pd.DataFrame(data={'tanimoto': tani_matrix,'i': i_column, 'k': k_column, 'validity':'valid'})
    df['above_tani_cutoff?'] = df['tanimoto'] >= minTanimotoSimilarity  
    df.loc[df['above_tani_cutoff?'] == False,'validity'] = 'invalid' 
    df_ranked = df.sort_values('tanimoto', ascending=False)
    #print('Tanimoto similarity matrix read and recorded. Starting clustering algorithm...')
    # main MultiMCS clustering algorithm implementation
    counter = 0
    all_clusters = []
    mcs_results_all = []
    mcs_mols_all = []
    # loop as long as there is a valid pair to be considered
    while_count = 0
    while len(df_ranked.loc[df_ranked['validity'] == 'valid']) != 0:
        while_count += 1
        # pick a valid pair that has the highest tanimoto validity
        index_in_df = df_ranked.loc[df_ranked['validity'] == 'valid','i'].index[0]
        i = i_column[index_in_df]
        k = k_column[index_in_df]
        ## THE FOLLOWING SECTION WAS REMOVED BECAUSE IT IS REDUNDANT, since all pairs below cutoff were tagged as invalid to begin with
        # if similarity of P is below the minTanimotoSimilarity cutoff, break. Should be the last occurence
        #if df_ranked.loc[df_ranked['validity'] == 'valid','tanimoto'].head(1).values < minTanimotoSimilarity:
            #print ('break occurred')
            #break
        # pick all valid molecules M whose similarity to both molecules in P exceeds the min TanimotoSimilarity
        df_valid = df_ranked.loc[df_ranked['validity'] == 'valid',:]
        df_picked = df_valid.loc[(df_valid['i'].isin([i,k])) | (df_valid['k'].isin([i,k])),:]
        df_qualified = df_picked.loc[df_picked['above_tani_cutoff?'] == True,:]
        M_set = np.unique(np.concatenate([df_qualified['i'].unique(),df_qualified['k'].unique()]))
        # mark the pair as invalid
        df_ranked.loc[(df_ranked['i'].isin([i,k])) | (df_ranked['k'].isin([i,k])),'validity'] = 'invalid'
        # If set of molecules found is smaller than minimum cluster size, restart loop.
        # my M_set already contains the P set too. so no need to -2 on minClusterSize'
        if len(M_set) < minClusterSize:
            #print('continuing loop for the %dth time with i and k as: ' %counter, i, k)
            counter += 1
            continue
        # find MCS of molecules in M_set, from SMILES list that was input, index-able by i nd k
        list_of_current_mols=[Chem.MolFromSmiles(smiles_list[index]) for index in M_set]
        mcs_result = rdFMCS.FindMCS(list_of_current_mols,
                                    completeRingsOnly=completeRingsOnly,
                                    ringMatchesRingOnly=ringMatchesRingOnly,
                                    atomCompare=atomCompare,
                                    bondCompare=bondCompare,
                                    ringCompare=ringCompare)
        # check # of atoms in MCS
        if mcs_result.numAtoms < minMCSSize:
            df_ranked.loc[(df_ranked['i'].isin(M_set)) | (df_ranked['k'].isin(M_set)),'validity'] = 'invalid'  
            counter += 1
        else:
            mcs_mol = Chem.MolFromSmarts(mcs_result.smartsString) # to use for substructure matching
            mcs_results_all.append(mcs_result) # for output
            mcs_mols_all.append(mcs_mol) # for output
            # do substructure search. H_set contains M_set by default and also other substructure matched molecules if any.
            H_set = list(M_set)
            for index,smiles in enumerate(smiles_list):
                if index in H_set:
                    continue
                if Chem.MolFromSmiles(smiles).GetSubstructMatch(mcs_mol) is not ():
                    H_set.append(index)
            new_cluster = H_set
            # compiling all clusters and labeling each element in M_set and H_set as invalid
            all_clusters.append(new_cluster)
            df_ranked.loc[(df_ranked['i'].isin(H_set)) | (df_ranked['k'].isin(H_set)),'validity'] = 'invalid'
            #print ('Cluster found (size %d) #%d : ' % (len(new_cluster),(len(all_clusters)-1)), new_cluster)
    #print('Total # of clusters found: %d' %len(all_clusters))
    # Any molecule in the input SMILES list that is NOT in a cluster, is considered a singleton
    length_of_clusters = len(all_clusters)
    singleton_list = []
    for index,smiles in enumerate(smiles_list):
        in_cluster = False
        for cluster in all_clusters:
            if index in cluster:
                in_cluster = True
        if in_cluster == False:
            singleton_list.append(index)
    #print ('Singletons (size %d) : ' %len(singleton_list), singleton_list)
    #print ('Clustering finished. Total while loop count=%d and total continue count=' %while_count, counter)               
    all_clusters.append(tuple(singleton_list)) #for output
    
    return all_clusters, mcs_mols_all, mcs_results_all, smiles_list, zinc_ids, length_of_clusters, df_ranked

res_temp = MultiMCS_clustering_nodup_noprint('list_of_100_smiles_right.txt',minTanimotoSimilarity=0.57, minClusterSize=3, minMCSSize=4)
res_temp[5]

6

In [4]:
# tani or distance calculator but gives a tril array
def tani_dist_calc_tril(input_file_path, distData=False):
    """
    """
    fps = []
    zinc_ids = []
    smiles_list = []
    counter = 0

    with open(input_file_path) as f:
        for line in f:
            smiles = line.split()[0] 
            zinc = line.split()[1]
            # check for duplicates
            if smiles not in smiles_list:
                # generate mol and fingerprint
                mol = Chem.MolFromSmiles(smiles)
                fp = Chem.RDKFingerprint(mol)
                # append to lists
                fps.append(fp)        
                zinc_ids.append(zinc)
                smiles_list.append(smiles)
                counter += 1
                if counter % 100 == 0:
                    sys.stdout.write('\rParsed %8d smiles' % counter)
                    sys.stdout.flush()

    print('Parsed %8d smiles' % counter)

    # first generate the distance matrix:
    #print('Generating distance matrix...')
    dists = []
    tani = []
    nfps = len(fps)      
    for i in range(nfps):
        sims = DataStructs.BulkTanimotoSimilarity(fps[i],fps[:i])
        sims.extend([1 for _  in range(nfps - i)])
        dists.append([1 - x for x in sims])
        tani.append([x for x in sims])
    if distData == True:
        return_metric = dists
    else: 
        return_metric = tani
    
    return return_metric
%time res_metric_new_2 = tani_dist_calc_tril('list_of_20_smiles_right.txt', distData=True)
len(res_metric_new_2)

df2 = pd.DataFrame(data=res_metric_new_2)#, index=range(17), columns=range(17))
#df2.head()

Parsed       17 smiles
Wall time: 57.3 ms


In [5]:
# tani or distance calculator but gives a tril array
def fp_list(input_file_path):
    """
    """
    fps = []
    zinc_ids = []
    smiles_list = []
    counter = 0

    with open(input_file_path) as f:
        for line in f:
            smiles = line.split()[0] 
            zinc = line.split()[1]
            # check for duplicates
            if smiles not in smiles_list:
                # generate mol and fingerprint
                mol = Chem.MolFromSmiles(smiles)
                fp = Chem.RDKFingerprint(mol)
                # append to lists
                fps.append(fp)        
                zinc_ids.append(zinc)
                smiles_list.append(smiles)
                counter += 1
                if counter % 100 == 0:
                    sys.stdout.write('\rParsed %8d smiles' % counter)
                    sys.stdout.flush()

    print('Parsed %8d smiles' % counter)
    return fps
%time res_fp_list = fp_list('list_of_20_smiles_right.txt')
len(res_fp_list)

#df2 = pd.DataFrame(data=res_metric_new_2)#, index=range(17), columns=range(17))
#df2
#res_fp_list

Parsed       17 smiles
Wall time: 55.8 ms


17

### Importing virtual screening data

In [6]:
input_file_path = 'list_of_1637_smiles_right.txt'

## MDS visualization section

#### First let's look at a set of ~1600 raw molecules. 

There are 1388 unique SMILES (duplicates being different 3D conformations). The clustering algorithms ignore duplicate SMILES, but later I can label all duplicates in the same cluster

In [7]:
df = pd.read_csv('list_of_1637_smiles_right.txt',header=None,names=['smiles','zinc_id'],delimiter='\t')
df.head()

smiles         zinc_id
0  O=c1ccc(CCc2nc([C@@H]3CCOC3)no2)n[nH]1  ZINC96164002_1
1       c1cncc(CCc2nc([C@@H]3CCOC3)no2)c1    ZINC96164165
2    Oc1cc(CCc2nc([C@@H]3CCOC3)n[nH]2)on1  ZINC97784960_1
3    Oc1cc(CCc2nc([C@@H]3CCOC3)n[nH]2)on1    ZINC97784960
4  O=c1ccc(CCc2nc([C@@H]3CCOC3)no2)n[nH]1    ZINC96164002

In [8]:
len(df), len(df['smiles'].unique())

(1637, 1388)

#### First let's visualize the chemical space of these molecules with MDS

In [9]:
#### MDS generation
input_file_path = 'list_of_1637_smiles_right.txt'
np.random.seed(42)

#calculating distance matrix
%time res_metric_new_2 = tani_dist_calc_tril(input_file_path, distData=True)
array = np.array(res_metric_new_2)
array_full = array.T + array

embedding = manifold.MDS(dissimilarity='precomputed')
%time transformed = embedding.fit_transform(array_full)
transformed
x_y_vals = transformed.transpose()
x_y_vals

Parsed     1300 smilesParsed     1388 smiles
Wall time: 5.98 s
Wall time: 2min 11s


array([[-0.52456781, -0.61826962, -0.52806501, ..., -0.04892535,
         0.06076146, -0.3770333 ],
       [ 0.33887704,  0.03457843,  0.39285216, ..., -0.32614185,
         0.05295108, -0.52574065]])

In [10]:
#### plotting section
height_val = 600
width_val = 900

p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Chemical space visualization of 1388 smiles with MDS'
    )
p.scatter(
        source=pd.DataFrame(data={'x': x_y_vals[0],'y': x_y_vals[1]}),#df.loc[df['cluster'] == cluster],
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

#### It looks pretty evenly distributed. I can't tell if that's a good thing or a bad thing. So I'll try color coding each point based on Butina clustering. I'll try a few different cutoff values to see how things change

## **Butina clustering with MDS**

#### Butina clustering seems to be a clustering algorithm solely(?) based on tanimoto similarity values between Daylight fingerprints. I guess people like to use it because it's already implemented in rdkit. For a purely ligand based approach, it seems suitable. It's very fast.

https://pubs.acs.org/doi/pdf/10.1021/ci9803381

#### First I wanted to test out some cutoff values, to see how many clusters they give

In [11]:
input_file_path = 'list_of_1637_smiles_right.txt'
cutoff_values = np.random.uniform(0,1,size=200)
num_of_clusters = []
for cutoff_val in cutoff_values:
    clusters, smiles, zinc_ids, length = butina_noprint(input_file_path,cutoff_val=cutoff_val)
    num_of_clusters.append(length)

Parsed     1300 smiles

In [12]:
p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Number of clusters vs Distance cutoff values',
    x_axis_label='Distance cutoff value',
    y_axis_label='Number of clusters'
    )
p.scatter(
        source=pd.DataFrame(data={'x': cutoff_values,'y': num_of_clusters}),
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

#### To not get too many clusters, I'll try out in the 0.8 to 0.6 range

In [13]:
#### CLUSTERING
input_file_path = 'list_of_1637_smiles_right.txt'
for cutoff_val in [0.8,0.75,0.7,0.65,0.6]:
    %time clusters, smiles_list, zinc_id_list, length = butina_noprint(input_file_path,cutoff_val)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded MDS visualization, showing Butina clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Parsed     1300 smilesWall time: 2.92 s
Cutoff value tested:  0.8
Total # of clusters:  5


Parsed     1300 smilesWall time: 3.08 s
Cutoff value tested:  0.75
Total # of clusters:  18


Parsed     1300 smilesWall time: 2.86 s
Cutoff value tested:  0.7
Total # of clusters:  45


Parsed     1300 smilesWall time: 2.86 s
Cutoff value tested:  0.65
Total # of clusters:  94


Parsed     1300 smilesWall time: 4.43 s
Cutoff value tested:  0.6
Total # of clusters:  145


#### I didn't think these results were that great. 0.65 seems the best, but it still has "spread-out" clusters. Butina seemed a bit hit or miss with its cutoff values, and seems to give either a few unevenly distributed clusters or too many fragmented, overlapping-ish clusters

### MultiMCS clustering with MDS

#### Now let's see how MultiMCS clusters raw 1388 SMILES. The algorithm uses tanimoto similarity to choose an initial set of molecules to calculate and MCS signature from. Then uses that MCS signature to do a substructure search, and clusters all hits. So a minimum tanimoto similarity gets to dictate which moleules are chosen for the initial MCS calculation. 

#### It has more parameters than butina, but I'll only test minTanimotoSimilarity here, and keep the rest at values I think give the best clustering and the best MCS signatures

In [14]:
input_file_path = 'list_of_1637_smiles_right.txt'
cutoff_values = np.random.uniform(0,1,size=200)
num_of_clusters = []
for cutoff_val in tqdm.tqdm(cutoff_values):
    clusters, mcs_mols, mcs_results, smiles_list, zinc_id_list, length, df_ranked = MultiMCS_clustering_nodup_noprint(input_file_path,
                                                                                minTanimotoSimilarity=cutoff_val, 
                                                                                minClusterSize=3, 
                                                                                minMCSSize=10,
                                                                                completeRingsOnly=False,
                                                                                ringMatchesRingOnly=True,
                                                                                atomCompare=rdFMCS.AtomCompare.CompareAny,
                                                                                bondCompare=rdFMCS.BondCompare.CompareOrder,
                                                                                ringCompare=rdFMCS.RingCompare.PermissiveRingFusion)
    num_of_clusters.append(length)

100%|██████████| 200/200 [2:10:38<00:00, 39.19s/it]  


In [15]:
p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Number of clusters vs Distance cutoff values',
    x_axis_label='Distance cutoff value',
    y_axis_label='Number of clusters'
    )
p.scatter(
        source=pd.DataFrame(data={'x': cutoff_values,'y': num_of_clusters}),
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

In [16]:
input_file_path = 'list_of_1637_smiles_right.txt'
for cutoff_val in [0.5,0.55,0.6,0.65,0.7]:
    #### CLUSTERING
    clusters, mcs_mols, mcs_results, smiles_list, zinc_id_list, length, df_ranked = MultiMCS_clustering_nodup_noprint(input_file_path,
                                                                                minTanimotoSimilarity=cutoff_val, 
                                                                                minClusterSize=3, 
                                                                                minMCSSize=10,
                                                                                completeRingsOnly=False,
                                                                                ringMatchesRingOnly=True,
                                                                                atomCompare=rdFMCS.AtomCompare.CompareAny,
                                                                                bondCompare=rdFMCS.BondCompare.CompareOrder,
                                                                                ringCompare=rdFMCS.RingCompare.PermissiveRingFusion)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded MDS visualization, showing MultiMCS clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Cutoff value tested:  0.5
Total # of clusters:  76


Cutoff value tested:  0.55
Total # of clusters:  96


Cutoff value tested:  0.6
Total # of clusters:  87


Cutoff value tested:  0.65
Total # of clusters:  79


Cutoff value tested:  0.7
Total # of clusters:  66


#### There's significant overlap of different clusters in all cases... For the most part, it doesn't look properly clustered. At least with an MDS represetation of the molecules. Also note that increasing minTanimotoSimilarity values give more and more singletons (light gray color)


## tSNE visualization

#### So instead of MDS, tSNE might be a better way of representing the chemical space of my molecules. It seems more complex.

In [17]:
#### MDS generation
input_file_path = 'list_of_1637_smiles_right.txt'
np.random.seed(42)

%time res_fp_list = fp_list(input_file_path)

#pca = PCA(n_components=80)
#%time crds = pca.fit_transform(res_fp_list)
#print ('PCA variance of first __ components: ', np.sum(pca.explained_variance_ratio_))

%time crds_embedded = manifold.TSNE(n_components=2).fit_transform(res_fp_list)
x_y_vals = crds_embedded.transpose()


Parsed     1300 smilesParsed     1388 smiles
Wall time: 2.42 s
Wall time: 25 s


In [18]:
#### plotting section
height_val = 600
width_val = 900

p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Chemical space visualization of 1388 smiles with tSNE'
    )

p.scatter(
        source=pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1]}),
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

#### It looks better than an MDS representation, like it has actual "clusters", definitely pleasing to look at. I'm hoping that means tSNE might be a better way of looking at my data. (and by extension UMAP, recommended by Jerome, since it's supposed to be better).

#### So I'll try visualizing the same clusterings by Butina and MultiMCS, but mapped onto the tSNE representation and see if that makes sense

### Butina clustering with tSNE

In [19]:
#### CLUSTERING
input_file_path = 'list_of_1637_smiles_right.txt'
for cutoff_val in [0.8,0.75,0.7,0.65,0.6]:
    %time clusters, smiles_list, zinc_id_list, length = butina_noprint(input_file_path,cutoff_val)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900
    
    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded tSNE visualization, showing Butina clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Parsed     1300 smilesWall time: 3.44 s
Cutoff value tested:  0.8
Total # of clusters:  5


Parsed     1300 smilesWall time: 2.79 s
Cutoff value tested:  0.75
Total # of clusters:  18


Parsed     1300 smilesWall time: 3.02 s
Cutoff value tested:  0.7
Total # of clusters:  45


Parsed     1300 smilesWall time: 4.69 s
Cutoff value tested:  0.65
Total # of clusters:  94


Parsed     1300 smilesWall time: 4.45 s
Cutoff value tested:  0.6
Total # of clusters:  145


#### Still looks pretty messy. Some clusters are spanning different local regions, and there is a lot of overlap. But some clusters look decently segregated from others, which is nice. Time to compare how MultiMCS looks like

### MultiMCS clustering with tSNE

In [20]:
input_file_path = 'list_of_1637_smiles_right.txt'
for cutoff_val in [0.5,0.55,0.6,0.65,0.7]:
    #### CLUSTERING
    clusters, mcs_mols, mcs_results, smiles_list, zinc_id_list, length, df_ranked = MultiMCS_clustering_nodup_noprint(input_file_path,
                                                                                minTanimotoSimilarity=cutoff_val, 
                                                                                minClusterSize=3, 
                                                                                minMCSSize=10,
                                                                                completeRingsOnly=False,
                                                                                ringMatchesRingOnly=True,
                                                                                atomCompare=rdFMCS.AtomCompare.CompareAny,
                                                                                bondCompare=rdFMCS.BondCompare.CompareOrder,
                                                                                ringCompare=rdFMCS.RingCompare.PermissiveRingFusion)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded tSNE visualization, showing MultiMCS clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Cutoff value tested:  0.5
Total # of clusters:  76


Cutoff value tested:  0.55
Total # of clusters:  96


Cutoff value tested:  0.6
Total # of clusters:  87


Cutoff value tested:  0.65
Total # of clusters:  79


Cutoff value tested:  0.7
Total # of clusters:  66


## **Murcko fragment clustering**

#### From here, I'll be clustering murcko fragments, instead of raw molecules. I'd performed the decomposition elsewhere and saved the Murcko SMILES in a list. There were 704 unique Murcko SMILES generated from 1388 molecule SMILES (which is from the ~1600 molecules). Lesser numbers and simpler SMILES might allow for easier and better clustering(?) 

In [21]:
#### MDS generation
input_file_path = 'list_of_1637_murcko.txt'
np.random.seed(42)

#calculating distance matrix
%time res_metric_new_2 = tani_dist_calc_tril(input_file_path, distData=True)
array = np.array(res_metric_new_2)
array_full = array.T + array

embedding = manifold.MDS(dissimilarity='precomputed')
%time transformed = embedding.fit_transform(array_full)
transformed
x_y_vals = transformed.transpose()
x_y_vals

Parsed      700 smilesParsed      704 smiles
Wall time: 1.41 s
Wall time: 18.9 s


array([[-0.00025679, -0.00025679,  0.00026541, ...,  0.02284801,
         0.03045434, -0.01615875],
       [ 0.03048186,  0.03048186,  0.10849345, ..., -0.03067462,
         0.0404069 , -0.12963186]])

In [22]:
#### plotting section
height_val = 600
width_val = 900

p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Chemical space visualization of 704 smiles with MDS'
    )
p.scatter(
        source=pd.DataFrame(data={'x': x_y_vals[0],'y': x_y_vals[1]}),#df.loc[df['cluster'] == cluster],
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

## **Butina clustering with MDS**

#### Same as last time, I wanted to see the number of clusters vs cutoff value plot to have an idea of what values to choose 

In [23]:
input_file_path = 'list_of_1637_murcko.txt'
cutoff_values = np.random.uniform(0,1,size=200)
num_of_clusters = []
for cutoff_val in cutoff_values:
    clusters, smiles, zinc_ids, length = butina_noprint(input_file_path,cutoff_val=cutoff_val)
    num_of_clusters.append(length)

Parsed      700 smiles

In [24]:
p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Number of clusters vs Distance cutoff values',
    x_axis_label='Distance cutoff value',
    y_axis_label='Number of clusters'
    )
p.scatter(
        source=pd.DataFrame(data={'x': cutoff_values,'y': num_of_clusters}),
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

#### Since range 0~0.2 seems to get clusters (at all), I'll try 5 values between there

In [25]:
#### CLUSTERING
input_file_path = 'list_of_1637_murcko.txt'
for cutoff_val in [0.25,0.2,0.15,0.1,0.05]:
    %time clusters, smiles_list, zinc_id_list, length = butina_noprint(input_file_path,cutoff_val)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded MDS visualization, showing Butina clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Parsed      700 smilesWall time: 1.16 s
Cutoff value tested:  0.25
Total # of clusters:  4


Parsed      700 smilesWall time: 2.56 s
Cutoff value tested:  0.2
Total # of clusters:  6


Parsed      700 smilesWall time: 1.17 s
Cutoff value tested:  0.15
Total # of clusters:  10


Parsed      700 smilesWall time: 1.16 s
Cutoff value tested:  0.1
Total # of clusters:  13


Parsed      700 smilesWall time: 1.16 s
Cutoff value tested:  0.05
Total # of clusters:  24


#### These results seem more reasonable than Butina clustering 1388 SMILES. But clusters still seem pretty "spread-out",, which isn't good.

### MultiMCS clustering with MDS

#### Now let's see how MultiMCS clusters 704 murcko SMILES. 

In [26]:
input_file_path = 'list_of_1637_murcko.txt'
cutoff_values = np.random.uniform(0,1,size=200)
num_of_clusters = []
for cutoff_val in tqdm.tqdm(cutoff_values):
    clusters, mcs_mols, mcs_results, smiles_list, zinc_id_list, length, df_ranked = MultiMCS_clustering_nodup_noprint(input_file_path,
                                                                                minTanimotoSimilarity=cutoff_val, 
                                                                                minClusterSize=3, 
                                                                                minMCSSize=10,
                                                                                completeRingsOnly=False,
                                                                                ringMatchesRingOnly=True,
                                                                                atomCompare=rdFMCS.AtomCompare.CompareAny,
                                                                                bondCompare=rdFMCS.BondCompare.CompareOrder,
                                                                                ringCompare=rdFMCS.RingCompare.PermissiveRingFusion)
    num_of_clusters.append(length)

100%|██████████| 200/200 [07:16<00:00,  2.18s/it]


In [27]:
p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Number of clusters vs Distance cutoff values',
    x_axis_label='Distance cutoff value',
    y_axis_label='Number of clusters'
    )
p.scatter(
        source=pd.DataFrame(data={'x': cutoff_values,'y': num_of_clusters}),
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

#### Since only REALLY high values give actual clusters, I'll see how those do

In [28]:
input_file_path = 'list_of_1637_murcko.txt'
for cutoff_val in [0.90,0.95,0.99]:
    #### CLUSTERING
    clusters, mcs_mols, mcs_results, smiles_list, zinc_id_list, length, df_ranked = MultiMCS_clustering_nodup_noprint(input_file_path,
                                                                                minTanimotoSimilarity=cutoff_val, 
                                                                                minClusterSize=3, 
                                                                                minMCSSize=10,
                                                                                completeRingsOnly=False,
                                                                                ringMatchesRingOnly=True,
                                                                                atomCompare=rdFMCS.AtomCompare.CompareAny,
                                                                                bondCompare=rdFMCS.BondCompare.CompareOrder,
                                                                                ringCompare=rdFMCS.RingCompare.PermissiveRingFusion)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded MDS visualization, showing MultiMCS clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Cutoff value tested:  0.9
Total # of clusters:  1


Cutoff value tested:  0.95
Total # of clusters:  4


Cutoff value tested:  0.99
Total # of clusters:  7


#### There's significant LITERAL overlap between different clusters. Which doesn't make sense. Might be a bug in the code that's allowing the same murcko SMILES to be assigned to multiple clusters. Or it could be that some murcko SMILES actually have a fingerprint similiarity of 1.


## tSNE visualization

#### So instead of MDS, tSNE might be a better way of representing the chemical space of my molecules. It seems more complex.

In [29]:
#### MDS generation
input_file_path = 'list_of_1637_murcko.txt'
np.random.seed(42)

%time res_fp_list = fp_list(input_file_path)

#pca = PCA(n_components=80)
#%time crds = pca.fit_transform(res_fp_list)
#print ('PCA variance of first __ components: ', np.sum(pca.explained_variance_ratio_))

%time crds_embedded = manifold.TSNE(n_components=2).fit_transform(res_fp_list)
x_y_vals = crds_embedded.transpose()


Parsed      700 smilesParsed      704 smiles
Wall time: 1.02 s
Wall time: 9.08 s


In [30]:
#### plotting section
height_val = 600
width_val = 900

p = bokeh.plotting.figure(
    width=width_val,
    height=height_val,
    title='Chemical space visualization of 704 murcko smiles with tSNE'
    )

p.scatter(
        source=pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1]}),
        x='x',
        y='y',
        size=5,
    )
bokeh.io.show(p)

#### It looks way better than an MDS representation, as it has clear defined islands, which I hope are clusters. Now if only the clustering algorithms would label them as clusters.

#### So I'll try visualizing the same clusterings by Butina and MultiMCS, but mapped onto the tSNE representation.

### Butina clustering with tSNE

In [31]:
#### CLUSTERING
input_file_path = 'list_of_1637_murcko.txt'
for cutoff_val in [0.25,0.2,0.15,0.1,0.05]:
    %time clusters, smiles_list, zinc_id_list, length = butina_noprint(input_file_path,cutoff_val)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded tSNE visualization, showing Butina clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Parsed      700 smilesWall time: 3.13 s
Cutoff value tested:  0.25
Total # of clusters:  4


Parsed      700 smilesWall time: 1.16 s
Cutoff value tested:  0.2
Total # of clusters:  6


Parsed      700 smilesWall time: 1.17 s
Cutoff value tested:  0.15
Total # of clusters:  10


Parsed      700 smilesWall time: 1.22 s
Cutoff value tested:  0.1
Total # of clusters:  13


Parsed      700 smilesWall time: 1.29 s
Cutoff value tested:  0.05
Total # of clusters:  24


#### Hmm Butina doesn't seem to differentiate well between the two large noticeable islands. At least the smaller "clusters" seem to be correctly assigned as clusters, which is good.

### MultiMCS clustering with tSNE

In [32]:
input_file_path = 'list_of_1637_murcko.txt'
for cutoff_val in [0.90,0.95,0.99]:
    #### CLUSTERING
    clusters, mcs_mols, mcs_results, smiles_list, zinc_id_list, length, df_ranked = MultiMCS_clustering_nodup_noprint(input_file_path,
                                                                                minTanimotoSimilarity=cutoff_val, 
                                                                                minClusterSize=3, 
                                                                                minMCSSize=10,
                                                                                completeRingsOnly=False,
                                                                                ringMatchesRingOnly=True,
                                                                                atomCompare=rdFMCS.AtomCompare.CompareAny,
                                                                                bondCompare=rdFMCS.BondCompare.CompareOrder,
                                                                                ringCompare=rdFMCS.RingCompare.PermissiveRingFusion)
    df = pd.DataFrame(data={'x': x_y_vals[0], 'y': x_y_vals[1], 'zinc_id': zinc_id_list, 'smiles': smiles_list,})
    df['index'] = df.index
    print ('Cutoff value tested: ', cutoff_val)
    print ('Total # of clusters: ', length)
    # labeling with cluster information
    for cluster_num,cluster in enumerate(clusters):
        if cluster == clusters[-1]:
            cluster_num = 'singleton'
        for index in cluster:
            df.loc[df['index'] == index,'cluster'] = str(cluster_num)
    cluster_names_df = df['cluster'].sort_values('index').unique()

    #### plotting section
    height_val = 600
    width_val = 900

    p = bokeh.plotting.figure(
        width=width_val,
        height=height_val,
        tooltips=[
            ('ZINC ID', '@zinc_id'),
            ('index', '@index'),
            ('cluster', '@cluster')
        ],
        title='Color coded tSNE visualization, showing MultiMCS clustering result'
        )
    color_list = itertools.cycle(palette1)
    for cluster, color in zip(cluster_names_df, color_list):
        if cluster == 'singleton':
            color='#cccccc'
        p.scatter(
            source=df.loc[df['cluster'] == cluster],
            x='x',
            y='y',
            size=5,
            color=color,
            legend_label=cluster
        )
    p.legend.click_policy = 'hide'
    bokeh.io.show(p)

Cutoff value tested:  0.9
Total # of clusters:  1


Cutoff value tested:  0.95
Total # of clusters:  4


Cutoff value tested:  0.99
Total # of clusters:  7


#### This is just gross, to be honest. At the same "island" murcko fragments are labeled as different clusters, which doesn't make sense. Something is not right when MultiMCS is used with murcko fragments.